# Book Tag Cleaning 

The focus of this notebook is to take a look at all the tags that we have present in our data set. From their we clean and normalize the tags, and start to determine what tags are in and out of scope. By the end we try to generalize some larger "parent" tags and also try to filter and join the tags with our larger "Books" dataset.

In [1]:
# Potentially missing imports

# !pip install googletrans
# !pip install distance

In [2]:
%matplotlib inline

#Utility Imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt


#Special Imports
from nltk.corpus import words
from googletrans import Translator
import string


#ML Imports
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
from sklearn.metrics import adjusted_rand_score
import sklearn.cluster
import distance

In [4]:


r = pd.read_csv( '../data/raw_data/ratings.csv' )
tr = pd.read_csv( '../data/raw_data/to_read.csv' )
b = pd.read_csv( '../data/raw_data/books.csv' )

t = pd.read_csv( '../data/raw_data/tags.csv' )
bt = pd.read_csv( '../data/raw_data/book_tags.csv')


In [5]:
t.shape

(34252, 2)

In [6]:
t_copy = t.copy()
t_copy.head()

tag_id tag_name
0       0        -
1       1     --1-
2       2    --10-
3       3    --12-
4       4   --122-

### Lowercase Tags

In [7]:
#Apply lower case normalization to all the tags
t_copy['tag_name'] = t_copy['tag_name'].apply(lambda x: x.lower())

In [8]:
# Initial cleaning 
for index, row in t_copy.iterrows():
    print(str(row['tag_id']) + " : " + row['tag_name'])    

0 : -
1 : --1-
2 : --10-
3 : --12-
4 : --122-
5 : --166-
6 : --17-
7 : --19-
8 : --2-
9 : --258-
10 : --3-
11 : --33-
12 : --4-
13 : --5-
14 : --51-
15 : --6-
16 : --62-
17 : --8-
18 : --99-
19 : --available-at-raspberrys--
20 : -2001--
21 : -calif--
22 : -d-c--
23 : -dean
24 : -england-
25 : -fiction
26 : -fictional
27 : -fictitious
28 : -football-
29 : -george
30 : -gr-
31 : -history
32 : -imaginary
33 : -italy-
34 : -la--
35 : -los
36 : -mass--
37 : -murder-
38 : -n-y--
39 : -non-poetry-
40 : -performing
41 : -post
42 : -psychology-
43 : -read
44 : -single
45 : -specific
46 : -television
47 : 0
48 : 0-0-0-0cant-find
49 : 0-0-bingo
50 : 0-4-star-rating
51 : 0-a-find-2016-summer-00
52 : 0-all2
53 : 0-best-picture-younger
54 : 0-boxed
55 : 0-c
56 : 0-eric-s-books
57 : 0-house-lbkc
58 : 0-kindle
59 : 0-love-funny
60 : 0-made-me-cry-moved-me
61 : 0-nonfiction
62 : 0-owned
63 : 0-paperback
64 : 0-pgs-200-to-299
65 : 0-physical-own
66 : 0-plays
67 : 0-plc
68 : 0-tbr-axz-usa
69 : 00-explori

1230 : 8
1231 : 8-5
1232 : 8-in-series
1233 : 8-kindle
1234 : 800
1235 : 800-201100
1236 : 800-literature
1237 : 800-poetry
1238 : 80s
1239 : 813-5
1240 : 82-93-children-juvenile-literature
1241 : 822-british-literature-drama
1242 : 8th-floor-library
1243 : 8th-grade
1244 : 8th-grade-books
1245 : 8th-grade-semester-2
1246 : 8th-in-series
1247 : 9
1248 : 9-11
1249 : 9-11-series
1250 : 9-12
1251 : 9-12-and-teen
1252 : 9-learn-great-acting
1253 : 9-sort
1254 : 9-stephen-king-green-mile
1255 : 90-minutes-in-heaven
1256 : 900-history-03-1600-1850
1257 : 900s
1258 : 90s
1259 : 911
1260 : 973-3
1261 : 973-7
1262 : 998
1263 : 9m
1264 : 9th-century
1265 : 9th-grade
1266 : 9th-grade-advisory
1267 : 9th-grade-reading-list
1268 : _
1269 : _3-4-class-library
1270 : __art
1271 : _audiobooks
1272 : _comics
1273 : _d
1274 : _essuy
1275 : _findinlibrary
1276 : _kindle
1277 : _leisure-non-fiction
1278 : _library_donations_
1279 : _libraryfind
1280 : _miscor2do
1281 : _non-series-04-06
1282 : _own-hard
1

2490 : andré-bella
2491 : andy
2492 : andy-andrews
2493 : andy-brazil
2494 : andy-brazil-series
2495 : andy-warhol
2496 : andy-weir
2497 : anecdotes
2498 : anf
2499 : angel
2500 : angel-books
2501 : angel-demon
2502 : angel-island
2503 : angel-series
2504 : angel-trilogy
2505 : angela
2506 : angela-carter
2507 : angela-hunt
2508 : angela-marsons
2509 : angela-s-favorites
2510 : angeles
2511 : angelfire
2512 : angelfire-series
2513 : angelic
2514 : angelology
2515 : angelou
2516 : angels
2517 : angels-and-demons
2518 : angels-and-dempns
2519 : angels-demons
2520 : angels-nephilim
2521 : angels-of-the-dark
2522 : angels-of-the-dark-series
2523 : anger
2524 : anger-management
2525 : angie-books
2526 : angie-sage
2527 : anglais
2528 : angles
2529 : angleske
2530 : anglo-americana
2531 : anglo-saxon
2532 : anglo-saxon-england
2533 : anglo-saxons
2534 : anglophilia
2535 : anglophones-vs-francophones
2536 : angry-robot
2537 : angry-teenager
2538 : angst
2539 : angstrom
2540 : angstrom-
2541 :

3720 : b-do-not-own
3721 : b-library
3722 : b-n
3723 : b-n-classics
3724 : b-n-leatherbound-classics
3725 : b-n-tbr-pics-7-22-17
3726 : b-philosophy-psychology-religion
3727 : b-visible-project
3728 : b1
3729 : b_comics
3730 : baatan-death-march
3731 : babak-s-shelves
3732 : babar
3733 : babe-ruth
3734 : babes
3735 : babies
3736 : babies-and-kids
3737 : babies-and-parenting
3738 : babies-and-toddlers
3739 : baby
3740 : baby-and-parenting
3741 : baby-baby
3742 : baby-books
3743 : baby-boy
3744 : baby-c-bookshelf
3745 : baby-care
3746 : baby-children
3747 : baby-for-the-billionaire
3748 : baby-library
3749 : baby-love
3750 : baby-parenting
3751 : baby-prep
3752 : baby-reads
3753 : baby-related
3754 : baby-s-books
3755 : baby-sitters-club
3756 : baby-sleep
3757 : baby-storytime
3758 : baby-stuff
3759 : baby-toddler
3760 : baby-trade
3761 : baby-wise
3762 : babysitter-s-club
3763 : babysitters
3764 : babysitters-club
3765 : babystuff
3766 : babytime
3767 : bach
3768 : bachman
3769 : back-b

4980 : book-fair-2015
4981 : book-fair-2017
4982 : book-finished
4983 : book-gals
4984 : book-gang
4985 : book-group
4986 : book-group-books
4987 : book-group-reads
4988 : book-groups
4989 : book-hangover
4990 : book-i-have-in-library
4991 : book-i-own
4992 : book-in-verse
4993 : book-into-movie
4994 : book-inventory
4995 : book-jawn-podcast
4996 : book-list-challenge
4997 : book-lovers-calendar
4998 : book-lust
4999 : book-lust-to-go
5000 : book-movie
5001 : book-movie-guide
5002 : book-of-ember
5003 : book-of-mormon
5004 : book-of-the-art
5005 : book-of-the-month
5006 : book-of-the-month-club
5007 : book-of-the-new-sun
5008 : book-on-cd
5009 : book-on-tape
5010 : book-order
5011 : book-peeps
5012 : book-project
5013 : book-read-a-long-time-ago
5014 : book-recommendations-for-clients
5015 : book-report
5016 : book-reports
5017 : book-research-stuff
5018 : book-riot
5019 : book-riot-books
5020 : book-riot-quarterly-box
5021 : book-riot-rec
5022 : book-sale
5023 : book-sale-to-buy
5024 

...

28859 : study-bibles
28860 : study-books
28861 : study-built-in
28862 : study-series
28863 : study-shelf-1
28864 : study_author-series
28865 : studying
28866 : stue
28867 : stuff-i-loved
28868 : stuff-that-hurt
28869 : stuffed-animals
28870 : stumbled-on
28871 : stunt-memoirs
28872 : stupid-book-made-me-cry
28873 : sturgeon
28874 : sturgis
28875 : sturm-und-drang
28876 : style
28877 : style-nouveau
28878 : styles
28879 : styron
28880 : stéphanie-plum
28881 : sub
28882 : sub-bücher
28883 : sub-read
28884 : subconscious
28885 : subculture
28886 : subcultures
28887 : subgenre-sf-dystopian-future
28888 : subject
28889 : subject-people
28890 : subject-vampire
28891 : subject-visual-arts
28892 : subliminal-mind-control
28893 : submarine
28894 : submarines
28895 : submission
28896 : submissive
28897 : subshelves
28898 : substance-abuse
28899 : subterranean
28900 : subtle-energy
28901 : suburban
28902 : suburbia
28903 : subways
28904 : success
28905 : success-25
28906 : success-books
28907 : s

30188 : the-wicked-years
30189 : the-wild-ones
30190 : the-winner-s-trilogy
30191 : the-winner-stands-alone
30192 : the-wire
30193 : the-witcher
30194 : the-witcher-saga
30195 : the-witcher-series
30196 : the-witches
30197 : the-wolf-gift-chronicles
30198 : the-wolves-of-mercy-falls
30199 : the-work-and-the-glory
30200 : the-years-of-lyndon-johnson
30201 : the-young-elites
30202 : the-zombie-room
30203 : thea-harrison
30204 : thearc
30205 : theater
30206 : theater-plays
30207 : theaters
30208 : theatre
30209 : theatre-and-plays
30210 : theatre-arts-and-entertainment
30211 : theatre-books
30212 : theatre-books-scripts
30213 : theatre-film-music
30214 : theatre-play
30215 : theatre-plays
30216 : theatre-scripts
30217 : theatre-scripts-and-analysis
30218 : theatrical
30219 : theatrical-plays
30220 : thebes
30221 : theft
30222 : theme
30223 : theme-cooking
30224 : theme-naughty
30225 : theme-science
30226 : theme-social-studies
30227 : theme-tigers
30228 : theme-yummy
30229 : theo
30230 : 

31439 : ukya
31440 : ultimate
31441 : ultimate-favorites
31442 : ultimate-marvel
31443 : ultimate-reading-list
31444 : ultimate-spider-man
31445 : ultimate-teen-reading-list
31446 : ultimate-universe
31447 : ultrafavorite-greatest-books-of-all
31448 : ultramarathon
31449 : ultrarunning
31450 : ulubione
31451 : umberto-eco
31452 : umjetnici-umjetnost
31453 : umjetnost
31454 : umw
31455 : un-categorized
31456 : un-finished
31457 : unabridged
31458 : unavailable
31459 : unavailable-in-bg
31460 : unbroken
31461 : uncategorized
31462 : uncathegorized
31463 : uncertainty
31464 : unclassifed
31465 : unclassified
31466 : uncle-rick
31467 : uncle-s-books
31468 : uncle-si
31469 : uncle-steve
31470 : uncle-stevie
31471 : uncompleted
31472 : undead
31473 : undead-series
31474 : undecided-or-not-interested
31475 : undeniable
31476 : undeniable-series
31477 : under-200
31478 : under-200-pages
31479 : under-250-pages
31480 : under-5
31481 : under-desk
31482 : under-suspicion
31483 : under-suspicion-s

32679 : woman-author
32680 : woman-s-fiction
32681 : woman-s-murder-club
32682 : woman-trans-agender-authors
32683 : womanhood
32684 : womans-literature
32685 : womans-murder-club
32686 : women
32687 : women-and-religion
32688 : women-authors
32689 : women-entrepeneurs
32690 : women-feminism
32691 : women-fiction
32692 : women-friends
32693 : women-friendships
32694 : women-in-medicine
32695 : women-in-translation
32696 : women-in-war
32697 : women-literature
32698 : women-murder-club
32699 : women-of-a-certain-age
32700 : women-of-color
32701 : women-of-faith
32702 : women-of-the-otherworld
32703 : women-of-the-otherworld-series
32704 : women-of-the-underworld
32705 : women-read
32706 : women-s
32707 : women-s-bible-study
32708 : women-s-fiction
32709 : women-s-health
32710 : women-s-history
32711 : women-s-issues
32712 : women-s-lit
32713 : women-s-literature
32714 : women-s-ministry
32715 : women-s-murder
32716 : women-s-murder-club
32717 : women-s-murder-club-series
32718 : women-s

33875 : شعر-و-ادبیات-ایرانی
33876 : شعر-و-خواطر
33877 : شعر-و-شاعری
33878 : شعر-و-نظم
33879 : شعر-وخواطر
33880 : شعر-پارسی
33881 : شعر-کلاسیک
33882 : شيرلوك-هولمز
33883 : شيكاجو
33884 : شيكاغو
33885 : صادق-هدایت
33886 : صانع-الظلام
33887 : صرخة-الرعب
33888 : صلاح-جاهين
33889 : صمد-بهرنگی
33890 : صوتيات
33891 : صوفى
33892 : طنز
33893 : طه
33894 : طه-الغريب
33895 : ظل-الافعى
33896 : ظل-اﻻفعي
33897 : ع
33898 : عائد-الى-حيفا
33899 : عائض-القرنى
33900 : عائض-القرني
33901 : عابر-سرير
33902 : عالم-الروايات
33903 : عالم-المعرفة
33904 : عام
33905 : عباس-معروفی
33906 : عبث
33907 : عبد-الله-المغلوث
33908 : عبدالله-المغلوث
33909 : عربى
33910 : عربي
33911 : عربي-ساخر
33912 : عربية
33913 : عز-الدين-شكرى
33914 : عز-الدين-شكرى-فشير
33915 : عز-الدين-شكري
33916 : عز-الدين-شكري-فشير
33917 : عز-الدين-فشير
33918 : عزازيل
33919 : عزالدين-شكرى-فشير
33920 : عزالدين-شكري-فشير
33921 : عصام-يوسف
33922 : عقاید-یک-دلقک
33923 : عقيدة
33924 : عك
33925 : علاء-الأسوانى
33926 : علاء-الأسواني
33927 : علاء-الاسوانى
33928

### Numeric + Punctuation Tags

From taking a physical breeze through the book tags at first glance we notice that our tags are in alpha numeric order. From this we start to distinguish sets of tag_ids that are either out of scope or lack proper meaning to our project with the given documentation on the data provided.

Before trying any fancy string parsing or regex rules on the words, I start with taking out these rows. That are simply just empty or numerical with punctuation.
* Rows [0 - 18]

In [9]:
for index, row in t_copy.iterrows():
    if index == 19:
        break
    print(str(row['tag_id']) + " : " + row['tag_name'])
    
#Get rid of the top 19 rows
t_copy = t_copy[19:]    

print(t_copy.shape)
t_copy.head()

0 : -
1 : --1-
2 : --10-
3 : --12-
4 : --122-
5 : --166-
6 : --17-
7 : --19-
8 : --2-
9 : --258-
10 : --3-
11 : --33-
12 : --4-
13 : --5-
14 : --51-
15 : --6-
16 : --62-
17 : --8-
18 : --99-
(34233, 2)


tag_id                     tag_name
19      19  --available-at-raspberrys--
20      20                      -2001--
21      21                     -calif--
22      22                       -d-c--
23      23                        -dean

### Non-English Tags

There is an entire chunks of tags that are in Greek and Arabic letters, as a sample we have gone ahead to use Google Translate public Python API to translate a sample of ~870 entries.

In [10]:
# #Arabic tags
# arabic_tags = list(t_copy['tag_name'][33363:34232])
# len(arabic_tags)

In [11]:
# type(arabic_tags)

In [12]:
# translator = Translator()
# arabic_translations = translator.translate(arabic_tags, dest='en')
# for translation in arabic_translations:
#     print(translation.origin, ' -> ', translation.text)


In [13]:
# t_copy[33381:33382]

In [14]:
# t_copy[33381:33382]['tag_name']

In [15]:
# translator = Translator()
# translator.translate(str(t_copy[33381:33382]['tag_name'])).text

In [16]:
# some_arabic_book_ids = bt[bt['tag_id'] == 33400]["goodreads_book_id"]
# list(some_arabic_book_ids)

In [17]:
# b[b['goodreads_book_id'].isin(some_arabic_book_ids)]

Arabic language books, and tags is one example of a speciality in the raw data. For our purposes of cluster analysis, and ultimately prediction based on the books and novels we are strudying bringing new unknown languages into the mix presents a challenge. To be able to make sound predictions and tuning our model to capture the variation of language, phenotics, and culture is a little out of scope for now. Therefore we will be filtering out books and tags that are not of "English" origin for our project. Therefore in the cleaning of our tags we will be getting rid of these types of tags.

In [18]:
#From the physical glance at our data we can simple filter by the row numbers, all non-enligsh tags
t_non_english = t_copy[(False == t_copy['tag_name'].str.match(r"^[a-zA-Z0-9$@$!%*?&#':;^\-—_,'\\/\". +()]+$"))]
t_non_english.shape

(1289, 2)

In [19]:
for index,row in t_non_english.iterrows():
    print(str(row["tag_id"]) + " : " + str(row["tag_name"]))

103 : 029-نجيب-محفوظ
125 : 07-まんが-ほか
280 : 101-à-lire-dans-sa-vie
328 : 14艺术美学
403 : 1907-sahin-library-şahi̇n-ki̇tapliği
559 : 1نجوم
568 : 2-háló-nagy
579 : 2-ضباط
702 : 2012-عربي
960 : 28-حرف
981 : 2ضباط
1013 : 3-نجوم
1288 : _sachbücher
1618 : administração
1634 : adquirido-y-no-leído
2201 : alyson-noël
2391 : amélie-nothomb
2420 : anaïs-nin
2421 : anbefalet-ikke-undersøgt
2489 : andré-agassi
2490 : andré-bella
2598 : animé
2733 : antiquité
2925 : arnaldur-indriðason
3185 : arturo-pérez-reverte
3196 : as-crónicas-de-gelo-e-fogo
3292 : astérix
3629 : autores-lusófonos
3859 : bande-dessinée
3861 : bandes-dessinées
3927 : barnebøker
4051 : bd-à-lire
4475 : bibliothèque
4512 : bildbände
4584 : biografía
4585 : biografías
4601 : biographies-memoirs‎
4625 : biográficos
4881 : bokmål
4883 : bolaño
5690 : brené-recommends
5810 : bronté
5811 : brontë
5812 : brontë-sisters
5813 : brontës
6042 : böcker-i-bokhylla
6043 : bücher
6044 : bücher-gelesen
6045 : bücherregal
6149 : camilla-läckberg
619

34221 : پائولو-کوئیلو
34222 : پارسی
34223 : ڤيرتيجو
34224 : کتاب
34225 : کتاب-های-فارسی
34226 : کتاب-کودک
34227 : کتابهای-مورد-علاقه-ام
34228 : کودک
34229 : کودک-و-نوجوان
34230 : کودکان
34231 : کودکان-و-نوجوانان
34232 : کودکانه
34233 : ۱
34234 : วรรณว-ภา
34235 : ℱａｖｏｒｉｔｅｓ
34236 : 中文
34237 : 叶红
34238 : 小說-奇幻小說
34239 : 日本
34240 : 日本文学
34241 : 日本語
34242 : 漫画
34243 : 골든
34244 : ﹏moonplus-reader﹏
34245 : ﺭﺿﻮﻯ-عاشور
34246 : ﻳﻮﺳﻒ-زيدان
34247 : ｃhildrens
34248 : ｆａｖｏｒｉｔｅｓ
34249 : ｍａｎｇａ
34250 : ｓｅｒｉｅｓ
34251 : ｆａｖｏｕｒｉｔｅｓ


In [20]:
#From the physical glance at our data we can simple filter by the row numbers, all non-enligsh tags
t_english = t_copy[(True == t_copy['tag_name'].str.match(r"^[a-zA-Z0-9$@$!%*?&#':;^\-—_,'\\/\". +()]+$"))]
t_english.shape

(32944, 2)

In [21]:
for index,row in t_english.iterrows():
    print(str(row["tag_id"]) + " : " + str(row["tag_name"]))

19 : --available-at-raspberrys--
20 : -2001--
21 : -calif--
22 : -d-c--
23 : -dean
24 : -england-
25 : -fiction
26 : -fictional
27 : -fictitious
28 : -football-
29 : -george
30 : -gr-
31 : -history
32 : -imaginary
33 : -italy-
34 : -la--
35 : -los
36 : -mass--
37 : -murder-
38 : -n-y--
39 : -non-poetry-
40 : -performing
41 : -post
42 : -psychology-
43 : -read
44 : -single
45 : -specific
46 : -television
47 : 0
48 : 0-0-0-0cant-find
49 : 0-0-bingo
50 : 0-4-star-rating
51 : 0-a-find-2016-summer-00
52 : 0-all2
53 : 0-best-picture-younger
54 : 0-boxed
55 : 0-c
56 : 0-eric-s-books
57 : 0-house-lbkc
58 : 0-kindle
59 : 0-love-funny
60 : 0-made-me-cry-moved-me
61 : 0-nonfiction
62 : 0-owned
63 : 0-paperback
64 : 0-pgs-200-to-299
65 : 0-physical-own
66 : 0-plays
67 : 0-plc
68 : 0-tbr-axz-usa
69 : 00-exploring-1
70 : 00-graphic-novels-read
71 : 00-in-class
72 : 00-to-read-00
73 : 00-to-read-02
74 : 0000
75 : 0000-to-buy
76 : 00000
77 : 0000_notverified
78 : 000src-su-25-11-3-x
79 : 000src-w-15-0

1169 : 5ara
1170 : 5b
1171 : 5cm
1172 : 5th
1173 : 5th-grade
1174 : 5th-grade-reading-list
1175 : 5th-graders
1176 : 5th-in-series
1177 : 5thsummerreading
1178 : 6
1179 : 6-in-series
1180 : 6-nonfiction-for-2018
1181 : 6-star-books
1182 : 6-stars
1183 : 6-travel-fiction-series
1184 : 60-s
1185 : 600-wales
1186 : 600s
1187 : 60_per_2017
1188 : 60s
1189 : 60s-decade
1190 : 616
1191 : 645-library-materials-for-children
1192 : 65-books
1193 : 65-books-for-your-20s
1194 : 65-books-to-read-in-your-20-s
1195 : 65-books-to-read-in-your-20s
1196 : 65-books-you-need-to-read-in-your-2
1197 : 658-0
1198 : 658-4
1199 : 66-no-longer-own
1200 : 6th-grade
1201 : 6th-grade-books
1202 : 6th-grade-q1
1203 : 6th-grade-q2
1204 : 6th-grade-reading-challenge
1205 : 6th-grade-shelf
1206 : 6th-grader-books
1207 : 7
1208 : 7-10-year-olds
1209 : 7-9
1210 : 7-9-
1211 : 7-art
1212 : 7-habits
1213 : 7-in-series
1214 : 7-nonfiction-reference
1215 : 7-not-intrested
1216 : 70-a-d
1217 : 70-s
1218 : 70-spy-thriller
121

2454 : and-the-mountains-echoed
2455 : and-the-shofar-blew
2456 : andalusia
2457 : anderson
2458 : anderson-cooper
2459 : andes
2460 : andes-mountains
2461 : andika-adil
2462 : andre
2463 : andre-aciman
2464 : andre-bella
2465 : andre-books
2466 : andre-dubus-iii
2467 : andre-norton
2468 : andrea
2469 : andrea-cremer
2470 : andrea-hirata
2471 : andrea-levy
2472 : andrew
2473 : andrew-becs
2474 : andrew-clements
2475 : andrew-davidson
2476 : andrew-gross
2477 : andrew-jackson
2478 : andrew-ng-recommendations
2479 : andrew-peterson
2480 : andrew-wiles
2481 : andrews
2482 : andrews--mary-kay
2483 : andrews-ilona
2484 : andrews-mary-kay
2485 : andrews-v-c
2486 : andrews-vc
2487 : androids
2488 : andrzej-sapkowski
2491 : andy
2492 : andy-andrews
2493 : andy-brazil
2494 : andy-brazil-series
2495 : andy-warhol
2496 : andy-weir
2497 : anecdotes
2498 : anf
2499 : angel
2500 : angel-books
2501 : angel-demon
2502 : angel-island
2503 : angel-series
2504 : angel-trilogy
2505 : angela
2506 : angela-

3745 : baby-care
3746 : baby-children
3747 : baby-for-the-billionaire
3748 : baby-library
3749 : baby-love
3750 : baby-parenting
3751 : baby-prep
3752 : baby-reads
3753 : baby-related
3754 : baby-s-books
3755 : baby-sitters-club
3756 : baby-sleep
3757 : baby-storytime
3758 : baby-stuff
3759 : baby-toddler
3760 : baby-trade
3761 : baby-wise
3762 : babysitter-s-club
3763 : babysitters
3764 : babysitters-club
3765 : babystuff
3766 : babytime
3767 : bach
3768 : bachman
3769 : back-burner
3770 : back-in-the-day
3771 : back-shelf
3772 : back-to-school
3773 : backlog
3774 : backpacking
3775 : backseated
3776 : backstabbers-unite
3777 : backwards
3778 : bacterial-meningitis
3779 : bad
3780 : bad-ass-bikers
3781 : bad-ass-girls
3782 : bad-books
3783 : bad-boy
3784 : bad-boy-bikers
3785 : bad-boy-good-girl
3786 : bad-boys
3787 : bad-day
3788 : bad-did-not-finish
3789 : bad-experience-4me
3790 : bad-girls-book-club
3791 : bad-girls-don-t-die
3792 : bad-girls-dont-die
3793 : bad-kitty
3794 : bad-k

5055 : bookclubread
5056 : bookclubs
5057 : bookcrossing
5058 : booker
5059 : booker-2012
5060 : booker-2013
5061 : booker-2014
5062 : booker-2015
5063 : booker-2016
5064 : booker-books
5065 : booker-longlist
5066 : booker-prize
5067 : booker-prize-2011
5068 : booker-prize-2013
5069 : booker-prize-2014
5070 : booker-prize-nominees
5071 : booker-prize-shortlist
5072 : booker-prize-winner
5073 : booker-prize-winners
5074 : booker-short-list
5075 : booker-shortlist
5076 : booker-shortlisted
5077 : booker-winner
5078 : booker-winners
5079 : bookers
5080 : bookgroup
5081 : bookies
5082 : bookish-baes
5083 : bookish-books
5084 : booklight-2
5085 : booklist
5086 : booklists
5087 : bookmarks
5088 : bookmusthave2017
5089 : bookouture
5090 : books
5091 : books-1-10
5092 : books-1-12
5093 : books-11-20
5094 : books-13-25
5095 : books-2010
5096 : books-2012
5097 : books-2013
5098 : books-2014
5099 : books-2015
5100 : books-2016
5101 : books-2017
5102 : books-3
5103 : books-about-animals
5104 : boo

...

27213 : series-brainship
27214 : series-bridgertons
27215 : series-cedar-cove
27216 : series-charlize-edwards
27217 : series-chronicles-of-nick
27218 : series-chronicles-of-vladimir-tod
27219 : series-clifford
27220 : series-complete
27221 : series-completed
27222 : series-cont
27223 : series-courtney
27224 : series-dark-hunter
27225 : series-dark-hunters
27226 : series-dark-tower
27227 : series-deer-lake
27228 : series-demonica
27229 : series-dexter
27230 : series-discworld
27231 : series-divergent
27232 : series-dragonlance
27233 : series-dresden-files
27234 : series-dune
27235 : series-ender
27236 : series-fables
27237 : series-fever
27238 : series-finished
27239 : series-first
27240 : series-flat-stanley
27241 : series-foundation
27242 : series-fully-complete
27243 : series-goosebumps
27244 : series-gossip-girl
27245 : series-guild-hunter
27246 : series-halo
27247 : series-hard-ink
27248 : series-harry-bosch
27249 : series-harry-potter-peripherals
27250 : series-highlander
27251 : 

28516 : stalin
28517 : stalin-american-history
28518 : stalingrad
28519 : stalinism
28520 : stalker
28521 : stalkers
28522 : stalking
28523 : stalled
28524 : stan-berenstain
28525 : stand-alone
28526 : stand-alone-books
28527 : stand-alone-novels
28528 : stand-alones
28529 : stand-by
28530 : stand-up
28531 : stand-up-comedian
28532 : standalone
28533 : standalones
28534 : stanford-prison-experiment
28535 : stanislaw-lem
28536 : stanza-c
28537 : stapleton-montgomery
28538 : star
28539 : star-child
28540 : star-trek
28541 : star-wars
28542 : star-wars-books
28543 : star-wars-books-i-own
28544 : star-wars-cannon
28545 : star-wars-canon
28546 : star-wars-collection
28547 : star-wars-disney-canon
28548 : star-wars-eu
28549 : star-wars-expanded-universe
28550 : star-wars-fiction
28551 : star-wars-legacy
28552 : star-wars-legends
28553 : star-wars-legends-novels
28554 : star-wars-new-canon
28555 : star-wars-new-jedi-order
28556 : star-wars-novels
28557 : star-wars-old-canon
28558 : star-wars-

29823 : the-great-war
29824 : the-greats
29825 : the-greeks
29826 : the-green-mile
29827 : the-grey-wolves
29828 : the-grey-wolves-series
29829 : the-grisha
29830 : the-gruffalo
29831 : the-guard
29832 : the-guardian
29833 : the-hacker-series
29834 : the-hangman-s-daughter
29835 : the-hangmans-daughter
29836 : the-happiness-project
29837 : the-happy-belly
29838 : the-hathaways
29839 : the-hathaways-series
29840 : the-heir
29841 : the-heir-chronicles
29842 : the-help
29843 : the-heroes-of-olympus
29844 : the-hoard
29845 : the-hobbit
29846 : the-hollow
29847 : the-hollow-series
29848 : the-hollows
29849 : the-hollows-series
29850 : the-holocaust
29851 : the-horror
29852 : the-horus-heresy
29853 : the-host
29854 : the-house-of-night
29855 : the-hulk
29856 : the-human-mind
29857 : the-hundred
29858 : the-hunger-games
29859 : the-hunger-games-trilogy
29860 : the-hunger-pains
29861 : the-i-love-books
29862 : the-i-wish-to-have-books
29863 : the-immortal-series
29864 : the-immortals
29865 : t

31129 : transitional
31130 : transitional-chapter
31131 : transitional-chapter-book
31132 : transitional-chapter-books
31133 : translated
31134 : translated-books
31135 : translated-by-me
31136 : translated-fiction
31137 : translated-in-greek
31138 : translated-manga-manhwa
31139 : translated-novels
31140 : translation
31141 : translations
31142 : transmetropolitan
31143 : transpersonal
31144 : transplantation
31145 : transportation
31146 : transylvania
31147 : trash
31148 : trashy
31149 : trashy-novels
31150 : trashy-reads
31151 : trashy-romance
31152 : trauma
31153 : trauma-counselors
31154 : trauma-recovery
31155 : travel
31156 : travel-adventure
31157 : travel-africa
31158 : travel-agent-challenge-books-read
31159 : travel-and-adventure
31160 : travel-and-exploration
31161 : travel-and-language
31162 : travel-books
31163 : travel-essays
31164 : travel-europe
31165 : travel-fiction
31166 : travel-france
31167 : travel-geography
31168 : travel-guide
31169 : travel-guides
31170 : trav

32393 : what-to-read-next-backup2
32394 : what-would-jesus-do
32395 : whats-cookin-good-lookin
32396 : whats-cooking
32397 : wheat-belly
32398 : whedon
32399 : whedonverse
32400 : wheel
32401 : wheel-of-time
32402 : wheel-of-time-series
32403 : when-i-found-you
32404 : when-i-was-a-child
32405 : when-i-was-a-kid
32406 : when-i-was-a-little
32407 : when-i-was-little
32408 : when-i-was-young
32409 : when-i-was-younger
32410 : when-kids-were-very-small
32411 : when-the-game-was-ours
32412 : when-the-wind-blows
32413 : when-we-were-very-young
32414 : where-offline
32415 : whimsical
32416 : whish-list
32417 : whispersync
32418 : whitbread
32419 : whitcoulls-top-100
32420 : white
32421 : white-collar
32422 : white-girl-problems
32423 : white-house
32424 : white-karen
32425 : white-rabbit-chronicles
32426 : whites
32427 : whitman-road-book-group
32428 : whitney-gracia-williams
32429 : who
32430 : who-done-it
32431 : who-dun-it
32432 : who-moved-my-cheese
32433 : whodunit
32434 : whodunnit
324

In [22]:
# keep tags that are only english tags
t_copy = t_copy[(True == t_copy['tag_name'].str.match(r"^[a-zA-Z0-9$@$!%*?&#':;^\-—_,'\\/\". +()]+$"))]
print(t_copy.shape)
t_copy.head()

(32944, 2)


tag_id                     tag_name
19      19  --available-at-raspberrys--
20      20                      -2001--
21      21                     -calif--
22      22                       -d-c--
23      23                        -dean

### Checkpoint ~~ 

In [23]:
# Initial cleaning
print(t_copy.shape)
for index, row in t_copy.iterrows():
    print(str(row['tag_id']) + " : " + row['tag_name'])    

(32944, 2)
19 : --available-at-raspberrys--
20 : -2001--
21 : -calif--
22 : -d-c--
23 : -dean
24 : -england-
25 : -fiction
26 : -fictional
27 : -fictitious
28 : -football-
29 : -george
30 : -gr-
31 : -history
32 : -imaginary
33 : -italy-
34 : -la--
35 : -los
36 : -mass--
37 : -murder-
38 : -n-y--
39 : -non-poetry-
40 : -performing
41 : -post
42 : -psychology-
43 : -read
44 : -single
45 : -specific
46 : -television
47 : 0
48 : 0-0-0-0cant-find
49 : 0-0-bingo
50 : 0-4-star-rating
51 : 0-a-find-2016-summer-00
52 : 0-all2
53 : 0-best-picture-younger
54 : 0-boxed
55 : 0-c
56 : 0-eric-s-books
57 : 0-house-lbkc
58 : 0-kindle
59 : 0-love-funny
60 : 0-made-me-cry-moved-me
61 : 0-nonfiction
62 : 0-owned
63 : 0-paperback
64 : 0-pgs-200-to-299
65 : 0-physical-own
66 : 0-plays
67 : 0-plc
68 : 0-tbr-axz-usa
69 : 00-exploring-1
70 : 00-graphic-novels-read
71 : 00-in-class
72 : 00-to-read-00
73 : 00-to-read-02
74 : 0000
75 : 0000-to-buy
76 : 00000
77 : 0000_notverified
78 : 000src-su-25-11-3-x
79 : 00

1322 : a-g-riddle
1323 : a-galaxy-far-far-away
1324 : a-game-of-thrones
1325 : a-gift
1326 : a-girl-detective
1327 : a-good-story-about-inhabitants-of-d
1328 : a-great-book-that-will-surely-make
1329 : a-gregory-maguire
1330 : a-have
1331 : a-historical-novel-about-building-t
1332 : a-j-banner
1333 : a-j-jacobs
1334 : a-kh-tawfik
1335 : a-kindle
1336 : a-kindle-owned-book
1337 : a-kitchen
1338 : a-l-jackson
1339 : a-little-golden-book
1340 : a-long-time-ago
1341 : a-long-walk-to-water
1342 : a-louise-l-hay
1343 : a-love-story
1344 : a-m-homes
1345 : a-male-fiction
1346 : a-man-named-dave
1347 : a-manette-ansay
1348 : a-mango-shaped-space
1349 : a-mano
1350 : a-mccall-smith
1351 : a-meredith-walters
1352 : a-modern-witch-series
1353 : a-must-for-beatle-fans
1354 : a-must-read
1355 : a-n-roquelaure
1356 : a-novel-in-short-stories
1357 : a-own
1358 : a-p
1359 : a-p-j-abdul-kalam
1360 : a-part-shelved
1361 : a-piece-of-me
1362 : a-r-t-about-many
1363 : a-real-hero-and-a-real-human-bean
136

2557 : animal-human-bond
2558 : animal-intelligence
2559 : animal-lover
2560 : animal-lovers
2561 : animal-mystery
2562 : animal-narrator
2563 : animal-non-fiction
2564 : animal-nonfiction
2565 : animal-pov
2566 : animal-related
2567 : animal-rescue
2568 : animal-rights
2569 : animal-s-perspective
2570 : animal-sounds
2571 : animal-spirit
2572 : animal-spirit-guides
2573 : animal-stories
2574 : animal-story
2575 : animal-studies
2576 : animal-tales
2577 : animal-totems
2578 : animal-welfare
2579 : animalia
2580 : animals
2581 : animals-and-pets
2582 : animals-and-wildlife
2583 : animals-cats
2584 : animals-dogs
2585 : animals-farm
2586 : animals-horses
2587 : animals-misc
2588 : animals-nature
2589 : animals-pets
2590 : animals-pets-fish-bugs-etc
2591 : animation
2592 : animation-books
2593 : anime
2594 : anime-bleach
2595 : anime-manga
2596 : animism
2597 : animu
2599 : anis-mansour
2600 : anita
2601 : anita-amirrezvani
2602 : anita-blake
2603 : anita-blake-series
2604 : anita-blake-v

3844 : ball-four
3845 : ballard
3846 : ballet
3847 : ballet-dancers
3848 : balletgirl
3849 : balloons
3850 : baltimore
3851 : balzac
3852 : bambi
3853 : banana-yoshimoto
3854 : band
3855 : band-of-brothers
3856 : banda-desenhada
3857 : bande-dessin-e
3858 : bande-dessinee
3860 : bandes-dessinees
3862 : bandini
3863 : bands
3864 : bane
3865 : bane-chronicles
3866 : bang
3867 : bangalore
3868 : banging-book-club
3869 : bangla
3870 : bangladesh
3871 : bank
3872 : bank-bailout
3873 : bank-foreclosures
3874 : bank-robbers
3875 : bank-robbery
3876 : bank-system
3877 : banking
3878 : bankruptcy
3879 : banks
3880 : banks-iain-m
3881 : banks-maya
3882 : banksy
3883 : banned
3884 : banned-book
3885 : banned-books
3886 : banned-challenged
3887 : banned-challenged-books
3888 : banned-or-challenged
3889 : banshee
3890 : banshees
3891 : bansky
3892 : bantam-war-books
3893 : banter
3894 : baptist
3895 : bar-code
3896 : bar-codes
3897 : barack
3898 : barack-obama
3899 : barbados
3900 : barbara
3901 : 

5146 : books-for-me
5147 : books-for-mom
5148 : books-for-my-children
5149 : books-for-my-classroom
5150 : books-for-new-students
5151 : books-for-sale
5152 : books-for-sale-from-my-bookstore
5153 : books-for-school
5154 : books-for-teaching
5155 : books-for-the-boys
5156 : books-for-work
5157 : books-for-writers
5158 : books-from-childhood
5159 : books-from-egypt
5160 : books-from-gilmore-girls
5161 : books-from-my-childhood
5162 : books-from-my-youth
5163 : books-grandma-read
5164 : books-home-to-read
5165 : books-i-adore
5166 : books-i-already-have-to-read
5167 : books-i-always-meant-to-read
5168 : books-i-borrowed
5169 : books-i-bought
5170 : books-i-couldn-t-continue
5171 : books-i-didn-t-finish
5172 : books-i-do-not-own
5173 : books-i-don-t-have
5174 : books-i-donated
5175 : books-i-dont-want-to-read
5176 : books-i-enjoyed-reading
5177 : books-i-got
5178 : books-i-had-to-get-rid-of
5179 : books-i-hated
5180 : books-i-have
5181 : books-i-have-at-home
5182 : books-i-have-collected


...

28054 : sociology-psychology
28055 : sociopath
28056 : sociopaths
28057 : sociopathy
28058 : socrates
28059 : soft-copy
28060 : soft-porn
28061 : soft-science-fiction
28062 : soft-skills
28063 : softcover
28064 : software
28065 : software-craftmanship
28066 : software-craftsmanship
28067 : software-dev
28068 : software-development
28069 : software-engineering
28070 : sohrab-sepehri
28071 : sold
28072 : soldier
28073 : soldier-son
28074 : soldier-son-trilogy
28075 : soldiers
28076 : sole-regret
28077 : solitude
28078 : solo
28079 : solving-problems
28080 : somalia
28081 : somalian-refugees
28082 : somalis
28083 : some-books-i-read-a-long-time-ago
28084 : some-day
28085 : some-luck
28086 : some-of-my-favorite-reads
28087 : someday
28088 : someday-fiction
28089 : someday-maybe
28090 : someone
28091 : someone-to-love
28092 : somerset
28093 : somerset-maugham
28094 : somerville-library
28095 : something-to-think-about
28096 : sometimes-never
28097 : somik
28098 : son
28099 : sondheim
28100 

29371 : tbr-ya
29372 : tbs
29373 : tbt
29374 : tc-boyle
29375 : tc-netforce
29376 : tcc-bookclub
29377 : tch-lrn-307
29378 : tch_lrn-307
29379 : tea
29380 : tea-and-water
29381 : teacher
29382 : teacher-books
29383 : teacher-resources
29384 : teacher-student
29385 : teacher-student-romance
29386 : teachers
29387 : teachers-and-teaching
29388 : teaching
29389 : teaching-and-learning
29390 : teaching-and-learning-307
29391 : teaching-art
29392 : teaching-books
29393 : teaching-education
29394 : teaching-english
29395 : teagarden
29396 : team
29397 : team-6
29398 : team-building
29399 : teams
29400 : teamwork
29401 : tear-jerker
29402 : tear-jerkers
29403 : teardrop
29404 : teardrop-series
29405 : tearjerker
29406 : tearjerkers
29407 : tears
29408 : tears-of-a-tiger
29409 : tears-of-tiger
29410 : teasing
29411 : teatre
29412 : teatro
29413 : tebeos
29414 : tebeos-indy
29415 : tebeos-superheroes
29416 : tebeos-usa
29417 : tebow
29418 : tech
29419 : tech-books
29420 : tech-fiction
29421 : t

30644 : to-read-contemporary-nonfic
30645 : to-read-cook-books
30646 : to-read-cookbook
30647 : to-read-cookbooks
30648 : to-read-cooking
30649 : to-read-creativity
30650 : to-read-culinary
30651 : to-read-design
30652 : to-read-discworld
30653 : to-read-doing
30654 : to-read-don-t-own
30655 : to-read-dont-own
30656 : to-read-drama
30657 : to-read-dystopian
30658 : to-read-ebook
30659 : to-read-economics
30660 : to-read-education
30661 : to-read-essays
30662 : to-read-eventually
30663 : to-read-fairy-tales
30664 : to-read-faith
30665 : to-read-fan
30666 : to-read-fandom
30667 : to-read-fantasy
30668 : to-read-fantasy-series
30669 : to-read-fantasy-ya
30670 : to-read-fantasyscifi
30671 : to-read-feminism
30672 : to-read-fiction
30673 : to-read-fiction-biography
30674 : to-read-fiction-medium
30675 : to-read-finance
30676 : to-read-financial
30677 : to-read-first
30678 : to-read-food
30679 : to-read-for-fun
30680 : to-read-for-leisure
30681 : to-read-funny
30682 : to-read-get
30683 : to-

31953 : visual-art-all-the-way
31954 : visual-arts
31955 : visual-companion
31956 : visual-companions
31957 : visual-culture
31958 : visual-design
31959 : visual-wonders
31960 : visualization
31961 : visualizing
31962 : visuals
31963 : vivek-booklist
31964 : viz
31965 : viz-media
31966 : vk
31967 : vlad
31968 : vlad-tod
31969 : vladimir-nabokov
31970 : vladimir-tod
31971 : vladimir-todd
31972 : vlogbrothers
31973 : vocab
31974 : vocabulary
31975 : vocal-music
31976 : voice
31977 : voice-trait
31978 : void
31979 : void-trilogy
31980 : volcano
31981 : volcanoes
31982 : voltaire
31983 : volunteer
31984 : vonnegut
31985 : vonnegut-kurt
31986 : voodoo
31987 : vorkosigan
31988 : vorkosigan-saga
31989 : vowell
31990 : voyages
31991 : voyages-extraordinaires
31992 : vp-1
31993 : vp-second-grade
31994 : vru
31995 : vsauce
31996 : vt-reading-challenge
31997 : vulkan
31998 : vvf-reading
31999 : vwa
32000 : w
32001 : w-bruce-cameron
32002 : w-g-sebald
32003 : w-p-kinsella
32005 : w-psychology
3200

33214 : z-unsorted
33215 : z10-hardbacks
33216 : z11-11-11
33217 : z_other
33218 : z_read-2014
33219 : zadie-smith
33220 : zafon
33221 : zahn
33222 : zaklinac
33223 : zambia
33224 : zamonia
33225 : zamonien
33226 : zane
33227 : zane-books
33228 : zap
33229 : zappos
33230 : zaque-s
33231 : zboxe1
33232 : zboxno2
33233 : zboxw5
33234 : zealand
33235 : zebra
33236 : zebra-historical-romance
33237 : zee
33238 : zeeke
33239 : zeitgeist-pop
33240 : zekranizowane
33241 : zelazny
33242 : zelazny-roger
33243 : zelda-fitzgerald
33244 : zen
33245 : zen-buddhism
33246 : zeno-clients
33247 : zeppelin
33248 : zi
33249 : zibe
33250 : ziegesar
33251 : zimbabwe
33252 : zionism
33253 : zodiac
33254 : zoe
33255 : zoe-heller
33256 : zoe-sugg
33257 : zoeken
33258 : zoella-book-club
33259 : zoey-redbird
33260 : zola
33261 : zola-emile
33262 : zombie
33263 : zombie-apocalypse
33264 : zombie-books
33265 : zombie-fiction
33266 : zombie-horror
33267 : zombie-novels
33268 : zombies
33269 : zombies-and-such
33270

"tag_name" column can have several generic tags and/or several user defined tags. The user defined tags can be totally custom and specific to that user. Therefore they are not very meaningful to us when trying to deduce high level genres from these tags. 

In [24]:
#Books and their Tags
bt.head()

goodreads_book_id  tag_id   count
0                  1   30574  167697
1                  1   11305   37174
2                  1   11557   34173
3                  1    8717   12986
4                  1   33114   12716

In [25]:
#Book Tags grouped to get popularity of tags
bt_grouped = bt.groupby(by='tag_id').size().reset_index(name='count').sort_values(by='count',ascending=False)
bt_grouped.head()

tag_id  count
30574   30574   9983
11557   11557   9881
22743   22743   9858
5207     5207   9799
8717     8717   9776

In [26]:
#Joined to capture count and tag_name
t_joined = t_copy.join(bt_grouped.set_index('tag_id'), on='tag_id').sort_values(by="count",ascending=False)
t_joined.head(20)

tag_id           tag_name  count
30574   30574            to-read   9983
11557   11557          favorites   9881
22743   22743              owned   9858
5207     5207        books-i-own   9799
8717     8717  currently-reading   9776
18045   18045            library   9415
22753   22753        owned-books   9221
11743   11743            fiction   9097
30521   30521             to-buy   8692
17213   17213             kindle   8316
9221     9221            default   8239
10197   10197              ebook   8054
20774   20774           my-books   7561
3389     3389          audiobook   7242
10210   10210             ebooks   7203
32586   32586          wish-list   7192
20849   20849         my-library   7000
3392     3392         audiobooks   6862
15169   15169              i-own   6670
1642     1642              adult   6604

### Custom User Tags

As we can see the top 5 popular tags are all rather meaningless to us, therefore we must parse a level deeper to determine genre level tags. Therefore we must take a look to clean out more custom tags, and determine the best high level tags

In [27]:
#Get rid of punctuations from the tags
t_joined["tag_name"] = [tag.translate(str.maketrans(string.punctuation, ' '*len(string.punctuation))) for tag in t_joined["tag_name"]]
print(t_joined.shape)
t_joined.head()

(32944, 3)


tag_id           tag_name  count
30574   30574            to read   9983
11557   11557          favorites   9881
22743   22743              owned   9858
5207     5207        books i own   9799
8717     8717  currently reading   9776

In [28]:
# Iterate by most popular tags going down
print(t_joined.shape)
for index, row in t_joined.iterrows():
    print(str(row["tag_id"]) + " : " + str(row["tag_name"]) + " : " + str(row["count"]))

(32944, 3)
30574 : to read : 9983
11557 : favorites : 9881
22743 : owned : 9858
5207 : books i own : 9799
8717 : currently reading : 9776
18045 : library : 9415
22753 : owned books : 9221
11743 : fiction : 9097
30521 : to buy : 8692
17213 : kindle : 8316
9221 : default : 8239
10197 : ebook : 8054
20774 : my books : 7561
3389 : audiobook : 7242
10210 : ebooks : 7203
32586 : wish list : 7192
20849 : my library : 7000
3392 : audiobooks : 6862
15169 : i own : 6670
1642 : adult : 6604
3371 : audio : 6548
11590 : favourites : 6422
22034 : novels : 5665
22689 : own it : 5514
8055 : contemporary : 5287
25151 : read in 2015 : 5239
27199 : series : 5080
10093 : e book : 4941
25152 : read in 2016 : 4940
25150 : read in 2014 : 4902
5090 : books : 4818
1659 : adult fiction : 4775
10094 : e books : 4616
25149 : read in 2013 : 4384
4949 : book club : 4365
3358 : audible : 4346
11305 : fantasy : 4259
26138 : romance : 4251
3379 : audio books : 4220
1416 : abandoned : 4168
21989 : novel : 4084
24960 : 

27472 : shapeshifter : 115
13366 : good books : 115
724 : 2013 releases : 114
3614 : autobiography biography : 114
9597 : distopia : 114
17807 : learning : 114
8209 : cooking : 114
19064 : manga and comics : 114
11784 : fiction horror : 114
24609 : pulitzer : 114
11906 : film : 113
33133 : young adult romance : 113
430 : 1940s : 113
11803 : fiction mystery : 113
5357 : books read in 2012 : 112
19659 : medicine : 112
2071 : all books : 112
25450 : really want to read : 112
25122 : read graphic novels : 112
16757 : junior fiction : 112
28533 : standalones : 111
860 : 2017 challenge : 111
6784 : child : 111
6745 : chick : 111
31741 : vampire romance : 111
2287 : american classics : 111
18670 : love triangles : 111
13596 : graphicnovel : 110
8491 : creativity : 110
6969 : childrens classics : 110
24447 : prose : 110
3169 : arts : 110
19141 : manga read : 110
28479 : spy novels : 110
5918 : bullying : 110
19165 : mangas : 110
25223 : read manga : 109
2593 : anime : 109
26371 : russia : 109


6104 : caldecott challenge : 36
1666 : adult mystery : 36
17234 : kindle first : 36
15816 : irish lit : 36
205 : 100 books to read before you die : 36
26772 : sci fi   fantasy : 36
9122 : dean : 36
22310 : on : 36
26830 : science books : 36
4197 : behavior : 36
15002 : hugo nominee : 36
2166 : alt history : 36
11202 : fallen angels : 36
9136 : deankoontz : 36
28254 : space travel : 36
28609 : steam punk : 35
25500 : recommend : 35
22896 : pal : 35
11240 : family read alouds : 35
3140 : arthurian : 35
20845 : my kindle books : 35
21799 : nonfiction science : 35
21825 : nope : 35
5413 : books to read in your 20s : 35
31250 : true : 35
7814 : comics i own : 35
8222 : cooking books : 35
29113 : swedish : 35
29473 : teen reads : 35
29112 : sweden : 35
2359 : amnesia : 35
21187 : natural history : 35
29506 : television : 35
10236 : econ : 35
10182 : easy reader : 35
26683 : scandinavian crime : 35
19171 : mangas read : 35
10828 : erotica romance : 35
24638 : pulitzer winner : 35
26221 : rome

15406 : in russian : 18
18498 : locus award : 18
5342 : books read 2017 : 18
17783 : leadership books : 18
29384 : teacher student : 18
5246 : books i read to my kids : 18
15417 : in the kitchen : 18
15984 : j sandford : 18
15024 : human behavior : 18
23900 : polish : 18
5053 : bookclub books : 18
25035 : read as a teen : 18
18258 : lisa gardner : 18
29908 : the legend of drizzt : 18
15265 : ii : 18
6748 : chick flick : 18
16450 : jodi picoult books : 18
24179 : predictable : 18
15521 : indonesian literature : 18
15706 : international relations : 18
6346 : cartoon : 18
16555 : john sandford prey series : 18
29759 : the dresden files : 18
3773 : backlog : 18
18119 : libs 642 : 18
6846 : childhood reading : 18
15517 : indonesian books : 18
5200 : books i loved as a kid : 18
25235 : read multiple times : 18
4696 : black dagger brotherhood : 18
25686 : religious books : 18
25185 : read in polish : 18
31357 : twd : 18
4578 : biografia : 18
15466 : indian books : 18
18519 : lokal : 18
7440 :

20111 : mind fuck : 12
15795 : iraq : 12
15441 : incomplete series : 12
11617 : february : 12
18909 : magic users : 12
2619 : ann mccaffrey : 12
27592 : sherlockian : 12
18447 : livros : 12
31159 : travel and adventure : 12
18036 : liberty : 12
26598 : sarah dessen : 12
19558 : mc romance : 12
19571 : mccall smith : 12
30375 : thriller mystery suspense : 12
26591 : sara shepard : 12
22452 : oprah bookclub : 12
3922 : barker : 12
11764 : fiction classic : 12
29849 : the hollows series : 12
27618 : shinigami : 12
17271 : kindleunlimited : 12
28480 : spy stories : 12
6521 : central asia : 12
27289 : series redwall : 12
7839 : comics superheroes : 12
31790 : vegan : 12
15976 : j patterson : 12
32208 : washington dc : 12
28510 : stage : 12
9315 : desi : 12
24270 : pretty little liars series : 12
24268 : pretty little liars : 12
15952 : j d  robb : 12
11116 : facebook : 12
20059 : military nonfiction : 12
14050 : hate to love : 12
11609 : fear : 12
17148 : kids library : 12
2483 : andrews il

...

18462 : llama : 1
18465 : llew s : 1
18466 : llibre : 1
18467 : lloyd : 1
18504 : loeb : 1
18502 : locus sf : 1
18493 : lockdown : 1
18492 : loch ness monster : 1
18491 : locavore : 1
18490 : location italy : 1
18489 : location work : 1
18487 : location living room console table : 1
18486 : location kitchen : 1
18485 : location g : 1
18484 : local spirit : 1
18483 : local library d : 1
18482 : local library : 1
18478 : loc usa : 1
18477 : lobbyists : 1
18475 : loaned : 1
18469 : lloyd jones : 1
18424 : littles : 1
18420 : little league world series : 1
18506 : loft library : 1
18333 : literary scholarship : 1
18362 : literatura romana : 1
18359 : literatura poesia : 1
18357 : literatura niemiecka : 1
18350 : literatura inglesa : 1
18345 : literatura espanola : 1
18343 : literatura espa ola : 1
18341 : literatura chilena : 1
18336 : literary thriller : 1
18331 : literary reference : 1
18419 : little league : 1
18330 : literary or critical theory : 1
18327 : literary fiction or classics 

17346 : kiyo fujiwara : 1
17325 : kisses from katie : 1
17345 : kiwi : 1
17342 : kitty hawk : 1
17339 : kittens : 1
17337 : kitchen princess series : 1
17336 : kitchen princess : 1
17335 : kitchen library : 1
17334 : kitchen garden : 1
17332 : kitchen 1 : 1
17376 : knitting crochet : 1
17378 : knitting stories : 1
17379 : knitting theme : 1
17380 : knjige : 1
17421 : korean authors : 1
17418 : koran : 1
17417 : koonz dean : 1
17412 : koomiksid : 1
17405 : komedi : 1
17404 : koll : 1
17403 : koleksiku : 1
17401 : koleksi dirumah : 1
17399 : kohta hirano : 1
17397 : kodus olemas : 1
17396 : kodansha : 1
17395 : kochen : 1
17393 : kocak : 1
17392 : kobo abe : 1
17389 : knut hamsun : 1
17386 : known authors : 1
17385 : knowledge management : 1
17327 : kitaplik : 1
17324 : kisses : 1
17590 : langston hughes : 1
17250 : kindle paid : 1
17265 : kindle unlimmited : 1
17264 : kindle unlimited tbr : 1
17262 : kindle unlimited books : 1
17261 : kindle unlimited audio : 1
17258 : kindle to loan : 

20582 : mozambique : 1
20581 : moyes jojo : 1
20605 : mt holly library : 1
20606 : mt pleasant library : 1
20607 : mt tbr 2017 : 1
20608 : mtv books : 1
20630 : multigenerational : 1
20629 : multiculturalism : 1
20626 : multicultural lit : 1
20625 : multicultural international : 1
20624 : multicultural education : 1
20623 : multicultural books : 1
20621 : multi generational saga : 1
20620 : multi generational : 1
20618 : muller : 1
20617 : mull : 1
20616 : mulbet bookshop : 1
20615 : muirwood trilogy : 1
20614 : muirwood : 1
20613 : mughal empire : 1
20612 : mughal : 1
20611 : mudbug : 1
20609 : much loved : 1
20580 : moyes : 1
20578 : moving box : 1
20632 : multiple : 1
20498 : mother : 1
20521 : motivational  : 1
20515 : mothers sons : 1
20514 : mothers daughters : 1
20513 : mothers and sons : 1
20509 : motherhood parenting : 1
20505 : mother nature : 1
20504 : mother goose : 1
20499 : mother and daughter : 1
20495 : most wanted : 1
20576 : movies watched : 1
20494 : most want to rea

10809 : erlendur sveinsson : 1
10807 : erlend loe : 1
10806 : eris : 1
10799 : erika johansen : 1
10795 : erich fromm : 1
10794 : erica stevens : 1
10793 : erica jong : 1
10792 : eric wilson : 1
10832 : erskine caldwell : 1
10833 : erstkontakt : 1
10837 : escape from furnace : 1
10838 : escape the ordinary 2015 : 1
10875 : espiritual : 1
10872 : espionage to read : 1
10867 : espionage crime : 1
10865 : esperanza rising : 1
10858 : espanha : 1
10855 : esoterismo : 1
10854 : esoterik : 1
10853 : esoterie : 1
10851 : esoteric spirituality : 1
10850 : esoteric philosophy or science : 1
10848 : escuela : 1
10847 : escritores mexicanos : 1
10844 : escola : 1
10843 : escher : 1
10841 : escapology reviews : 1
10840 : escapism : 1
10839 : escaped convict : 1
10975 : eventyr kunst : 1
10981 : everneath series : 1
11132 : faeriewalker series : 1
11073 : expose : 1
11084 : eye candy : 1
11083 : eya : 1
11082 : extreme sports : 1
11081 : extreme horror : 1
11080 : extraterrestrial : 1
11078 : extra

14042 : hasht : 1
14041 : has not aged well : 1
14040 : harvey : 1
14039 : harvath  : 1
14037 : harvard compact : 1
14032 : haruf kent : 1
14030 : hart john : 1
14028 : harry potter : 1
14133 : healing touch : 1
14136 : health and cooking : 1
14298 : hermaphrodite : 1
14240 : hellsing : 1
14252 : hemingway ernest : 1
14250 : helping : 1
14249 : helpful research : 1
14248 : helpful : 1
14247 : help yourself : 1
14245 : help me : 1
14244 : help for the haunted : 1
14241 : helmet 2017 : 1
14238 : hellchaser : 1
14225 : helen hooven santmyer : 1
14237 : hellboy universe : 1
14234 : hellblazer : 1
14233 : hell s : 1
14231 : helene hanff : 1
14230 : helena hunting : 1
14229 : helena : 1
14228 : helen simonson : 1
14227 : helen keller : 1
14253 : hemingway list : 1
14257 : henri charriere : 1
14258 : henri nouwen : 1
14259 : henrietta lacks : 1
14293 : herman hesse : 1
14292 : herlezen : 1
14291 : heritage of shannara : 1
14290 : heritage of lancaster county series : 1
14286 : heresy : 1
1428

In [29]:
#Somewhat rudementary but this works! To get rid of a solid chunk of custom tags.
user_tags1 = 'to read+|reading+|my books+|wish list+|novel+|series+|^[[:digit:]]*$|i own+|currently+|own+|have+|[^[:alnum:] ]|favorite+|favourite+|'
user_tags2 = 'club+|buy+|library+|read+|borrowed+|abandoned+|audio+|ya|e book+|ebook+|kindle+|default+|finish+|maybe+|gave up+|'
user_tags3 = 'dnf+|stars+|^(15|16|17|18|19|20)\d{2}[a-zA-Z]*|century+|grade+'

user_tags = user_tags1+user_tags2 + user_tags3

del_filter = t_joined["tag_name"].str.contains(user_tags)

print(t_joined[del_filter].shape)
# Iterate by most popular tags going down
for index, row in t_joined[del_filter].iterrows():
    print(str(row["tag_id"]) + " : " + str(row["tag_name"]) + " : " + str(row["count"]))
    


(5790, 3)
30574 : to read : 9983
11557 : favorites : 9881
22743 : owned : 9858
5207 : books i own : 9799
8717 : currently reading : 9776
18045 : library : 9415
22753 : owned books : 9221
30521 : to buy : 8692
17213 : kindle : 8316
9221 : default : 8239
10197 : ebook : 8054
20774 : my books : 7561
3389 : audiobook : 7242
10210 : ebooks : 7203
32586 : wish list : 7192
20849 : my library : 7000
3392 : audiobooks : 6862
15169 : i own : 6670
3371 : audio : 6548
11590 : favourites : 6422
22034 : novels : 5665
22689 : own it : 5514
25151 : read in 2015 : 5239
27199 : series : 5080
10093 : e book : 4941
25152 : read in 2016 : 4940
25150 : read in 2014 : 4902
10094 : e books : 4616
25149 : read in 2013 : 4384
4949 : book club : 4365
3379 : audio books : 4220
1416 : abandoned : 4168
21989 : novel : 4084
24960 : re read : 3903
14064 : have : 3846
3377 : audio book : 3776
5481 : borrowed : 3674
25148 : read in 2012 : 3661
9477 : did not finish : 3420
11497 : favorite : 3363
19524 : maybe : 3243
27

/opt/anaconda3/lib/python3.7/site-packages/pandas/core/strings.py:344: FutureWarning: Possible nested set at position 56
  regex = re.compile(pat, flags=flags)
/opt/anaconda3/lib/python3.7/site-packages/pandas/core/strings.py:1843: UserWarning: This pattern has match groups. To actually get the groups, use str.extract.
  return func(self, *args, **kwargs)



19530 : maybe read : 193
22696 : own kindle : 192
894 : 2017 reading list : 185
26752 : school reading : 184
5231 : books i read as a kid : 184
785 : 2015 releases : 180
25761 : required reading : 179
10213 : ebooks i own : 175
5358 : books read in 2013 : 175
25191 : read in school : 170
2106 : all time favourites : 170
22674 : own ebook : 169
450 : 1960s : 168
22643 : own a copy : 168
659 : 2010 reads : 164
833 : 2016 releases : 163
13583 : graphic novels read : 162
21915 : not finished : 162
371 : 1800s : 161
14523 : historical novel : 161
12034 : first in a series : 160
442 : 1950s : 159
14524 : historical novels : 159
22813 : owned tbr : 155
8084 : contemporary ya : 154
807 : 2016 books read : 153
30811 : to read series : 150
7843 : comics to read : 150
609 : 2003 : 149
30800 : to read sci fi : 148
753 : 2014 releases : 148
13552 : graphic novel comics : 147
21948 : not owned : 144
30620 : to read business : 143
33007 : ya dystopian : 142
22009 : novela : 142
13567 : graphic novel

31730 : vampire diaries series : 8
14378 : high school reading : 8
8170 : cookbooks i have : 8
2887 : argeneau series : 8
20300 : modern library top 100 novels : 8
20353 : mom library : 8
19822 : merry gentry series : 8
19809 : meredith gentry series : 8
26279 : rosemary beach series : 8
8865 : dan brown : 8
19888 : michael bennett series : 8
24490 : psy changeling series : 8
4621 : biography to read : 8
17387 : known authurs : 8
5724 : bridgerton series : 8
30761 : to read on kindle : 8
30690 : to read health : 8
5354 : books read in 2009 : 8
4604 : biographies to read : 8
17097 : kid s library : 8
25131 : read historical fiction : 8
17172 : kids ya : 8
30711 : to read kids : 8
30579 : to read 2015 : 8
4956 : book club 2016 : 8
30612 : to read biographies : 8
30726 : to read longlist : 8
25109 : read for book club : 8
2842 : arabic read : 7
10496 : elvis cole series : 7
25049 : read before 2009 : 7
25369 : reading challenge 2016 : 7
6867 : children books read : 7
25052 : read before 2

27427 : shadow falls series : 5
27425 : shadow children series : 5
17141 : kids favorites : 5
11362 : fantasy novels : 5
5250 : books i read with my kids : 5
33033 : ya nonfiction : 5
481 : 1987 : 5
482 : 1988 : 5
484 : 1990 : 5
27228 : series demonica : 5
33027 : ya lit class : 5
5382 : books that i have : 5
27220 : series complete : 5
10966 : eve duncan series : 5
27307 : series sword of truth : 5
11745 : fiction 20th century : 5
11108 : fablehaven series : 5
11107 : fablehaven : 5
27273 : series lucas davenport : 5
22463 : oprahbookclub : 5
11044 : expanse series : 5
11808 : fiction novel : 5
5365 : books read to my kids : 5
434 : 1945  : 5
13126 : get from library : 5
30646 : to read cookbook : 5
32257 : we need diverse books : 5
9402 : dexter series : 5
4960 : book club choices : 5
13088 : georgina kincaid series : 5
13439 : gossip girl series : 5
28585 : started but not finished : 5
32123 : want to reread : 5
10008 : dune books : 5
12706 : future reads : 5
1357 : a own : 5
28168 

...

14420 : himalayas : 2
12036 : first in series manga : 2
8956 : dark swan series : 2
8959 : dark tower extended reading order : 2
26385 : russian novels : 2
8139 : cookbook i own : 2
10953 : evanovich full series : 2
11867 : fifty shades series : 2
7846 : comicsread : 2
28584 : started but never finished : 2
11863 : fifth grade : 2
7842 : comics to buy : 2
27681 : short stories to read : 2
9951 : drowning : 2
13453 : gothic novel : 2
10989 : everyman s library : 2
28571 : starcrossed series : 2
7795 : comics comic books graphic novels : 2
27265 : series kenzie gennaro : 2
9926 : drenai series : 2
12784 : gail tsukiyama : 2
28574 : stark series : 2
9197 : decided not to read : 2
27252 : series honorverse : 2
27253 : series i love : 2
27254 : series i need to finish : 2
27667 : short read : 2
27232 : series dragonlance : 2
14537 : historical ya : 2
26427 : s brown : 2
27208 : series book 3 : 2
27210 : series book 5 : 2
7923 : completed reading : 2
13490 : grade 8 : 2
7901 : companion nove

29962 : the missing series : 1
29959 : the mind readers series : 1
25172 : read in highschool : 1
25173 : read in hungarian : 1
25174 : read in icelandic : 1
29287 : taschen basic art series : 1
29914 : the life of women in royal family o : 1
29913 : the library of ridge and michelle : 1
29278 : target book club : 1
25159 : read in china : 1
25160 : read in class 4 : 1
25837 : rg reading challenge : 1
25165 : read in elementary : 1
25229 : read mary higgins clark : 1
25298 : read this year : 1
25299 : read to alex : 1
25300 : read to babies : 1
25301 : read to buy : 1
29787 : the fault in our stars : 1
25303 : read to chris : 1
25304 : read to kara : 1
25735 : renovel : 1
25306 : read to lil : 1
25307 : read to londyn : 1
29781 : the fallen series : 1
25297 : read this next : 1
25296 : read this a long time ago : 1
25282 : read sf : 1
25283 : read short stories : 1
25285 : read spirituality : 1
25286 : read sports : 1
25288 : read status unknown : 1
25289 : read stephen king : 1
25291 

24630 : pulitzer prize novels : 1
30535 : to check from library : 1
30533 : to buy used : 1
30532 : to buy soon : 1
24637 : pulitzer to read : 1
30530 : to buy one day : 1
30529 : to buy manga : 1
30634 : to read civil war : 1
30619 : to read bookshelf : 1
30617 : to read books adopted to film : 1
30616 : to read book : 1
30614 : to read biography memoir : 1
30611 : to read bio : 1
30610 : to read biblioteca : 1
30609 : to read based on : 1
30608 : to read barker : 1
30606 : to read available : 1
30632 : to read christianity : 1
28883 : sub read : 1
30627 : to read chic lit : 1
30626 : to read career : 1
30625 : to read c : 1
30623 : to read but dont own : 1
30622 : to read business success leadership : 1
30605 : to read authors : 1
30591 : to read again and again : 1
30589 : to read about a girl : 1
30587 : to read   non fiction : 1
30586 : to read 5 : 1
30603 : to read audio : 1
30584 : to read 2017 q1 : 1
30583 : to read 2017 nonfiction : 1
30582 : to read 2017 and beyond : 1
30576 

653 : 2010 books read : 1
651 : 2010 book list : 1
650 : 2010 book challenge : 1
649 : 2010 and earlier : 1
647 : 2010 2011 : 1
646 : 2010 100 : 1
795 : 2016 52 in 52 : 1
796 : 2016 60 books : 1
797 : 2016 and before read that i own : 1
886 : 2017 publication : 1
908 : 2017 horror : 1
907 : 2017 august horror : 1
906 : 2017 want to reads : 1
903 : 2017 to read list : 1
900 : 2017 summer reading list : 1
898 : 2017 reread : 1
891 : 2017 read women : 1
887 : 2017 re read : 1
885 : 2017 potentials : 1
798 : 2016 audiobooks : 1
884 : 2017 possible books : 1
880 : 2017 plan : 1
878 : 2017 new age : 1
877 : 2017 need to buy : 1
876 : 2017 must read : 1
875 : 2017 movies : 1
874 : 2017 may library book sale : 1
873 : 2017 manga : 1
909 : 2017 horror tbr challenge : 1
910 : 2017 mount tbr : 1
911 : 2017 reads : 1
912 : 2017bookshelf : 1
944 : 21st century lit : 1
942 : 21st century australian literature : 1
937 : 21 books every woman should read : 1
934 : 20th century post ww2 : 1
929 : 20th c

18171 : lifetime must reads : 1
18202 : lili s lifetime reads : 1
18189 : light vacation reads : 1
18185 : light novels : 1
18184 : light novel : 1
19118 : manga light novel : 1
19101 : manga graphic and visual novels : 1
19082 : manga comic to read : 1
19096 : manga favourites : 1
19089 : manga completed series : 1
19130 : manga manhwa read : 1
19167 : mangas comics graphic novels : 1
19159 : manga to buy : 1
19138 : manga or graphic novels : 1
19084 : manga comics and graphic novels : 1
19081 : manga comic graphic novel : 1
19067 : manga and light novels : 1
19066 : manga and graphic novels and comics : 1
19282 : mark read : 1
19207 : marasmania library : 1
18774 : lying game series : 1
18815 : mabey read : 1
18707 : ls guys read nominees : 1
18738 : lukyanenko : 1
18727 : lucky series : 1
18726 : lucky santangelo series : 1
18825 : macher library : 1
18958 : makara lending library : 1
18962 : makes you shit down both legs : 1
18963 : makes you stop reading and wonder : 1
18976 : mal

In [30]:
# Iterate by most popular tags going down
print(t_joined[~del_filter].shape)
for index, row in t_joined[~del_filter].iterrows():
    print(str(row["tag_id"]) + " : " + str(row["tag_name"]) + " : " + str(row["count"])) 

(27154, 3)
11743 : fiction : 9097
1642 : adult : 6604
8055 : contemporary : 5287
5090 : books : 4818
1659 : adult fiction : 4775
3358 : audible : 4346
11305 : fantasy : 4259
26138 : romance : 4251
20939 : mystery : 3686
1691 : adventure : 3661
33114 : young adult : 3630
10644 : english : 3625
9886 : drama : 3046
18367 : literature : 3005
12948 : general fiction : 2974
7457 : classics : 2785
8067 : contemporary fiction : 2696
14487 : historical fiction : 2590
22944 : paperback : 2566
14467 : historical : 2544
30358 : thriller : 2522
26785 : sci fi fantasy : 2467
2277 : american : 2463
29076 : suspense : 2419
25822 : reviewed : 2399
26771 : sci fi : 2227
26837 : science fiction : 2222
1540 : action : 2172
15048 : humor : 2161
11221 : family : 2160
14552 : history : 2138
21689 : non fiction : 2128
6122 : calibre : 2086
8517 : crime : 2083
11370 : fantasy sci fi : 1991
21815 : nook : 1987
6750 : chick lit : 1974
22973 : paranormal : 1941
26735 : school : 1940
7404 : classic : 1939
18886 : 

11226 : family drama : 224
27170 : sequels : 224
18011 : lgbtq : 224
23798 : pnr uf : 224
24224 : preschool : 223
23993 : popular fiction : 223
19316 : marriage : 223
31859 : victorian : 223
4634 : bios : 223
22376 : on the shelf : 223
28466 : spy : 222
26246 : rory gilmore : 221
10245 : economics : 220
31614 : urban : 220
26163 : romance paranormal : 219
10316 : educational : 217
6184 : canadian : 217
8507 : creepy : 215
32812 : world war ii : 214
17080 : kick ass heroine : 212
21195 : nature : 211
24521 : psychological thriller : 211
13098 : german : 211
8518 : crime and mystery : 210
14539 : historicalfiction : 210
19083 : manga comics : 210
28031 : social science : 208
8740 : cute : 208
15215 : ibooks : 206
11379 : fantasy sf : 206
19634 : medical : 206
2690 : anthology : 205
11136 : fairies : 204
31359 : tween : 204
4607 : biography and memoir : 203
20159 : misc : 203
31417 : uf : 201
2766 : apocalypse : 200
7094 : christian books : 200
2294 : american fiction : 200
32906 : ww2 : 

3259 : assassin : 62
5606 : brain : 62
27919 : slavery : 62
13235 : girls : 62
21337 : net galley : 62
27927 : sleuths : 62
4546 : billionaires : 62
28354 : spiritual formation : 62
19452 : mathematics : 62
5971 : business economics : 61
2499 : angel : 61
15646 : insta love : 61
26039 : roberts : 61
13922 : happiness : 61
7756 : comic fantasy : 61
27734 : siblings : 61
2595 : anime manga : 61
19030 : man booker prize : 61
3711 : b : 61
9184 : debut : 61
26436 : s king : 61
5140 : books for children : 61
7577 : coaching : 60
29462 : teen fantasy : 60
27062 : seen the movie : 60
23569 : physics : 60
25490 : recipes : 60
9097 : dc vertigo : 60
17415 : koontz dean : 60
17645 : latin american literature : 60
20405 : monsters : 59
6098 : caldecott : 59
27640 : shojo : 59
1033 : 33 keepers : 59
5295 : books made into movies : 59
10221 : ece 3601 : 59
31831 : vertigo comics : 59
28183 : south : 59
4637 : bios memoirs : 59
4612 : biography autobiography memoir : 59
24771 : quirky : 59
23552 : p

17735 : lawyer : 40
2713 : anti hero : 40
17748 : lds author : 40
19077 : manga collection : 40
18697 : low fantasy : 40
21472 : newbery medal winners : 39
3179 : artsy : 39
8162 : cookbooks food : 39
10655 : english history : 39
26422 : s : 39
14877 : horses : 39
14456 : historia : 39
7391 : class : 39
19860 : mexico : 39
28648 : stephen : 39
19166 : mangas comics : 39
23353 : personal mba : 39
14999 : hugo nebula : 39
11425 : fashion : 39
11949 : financial : 39
9535 : dirty talk : 39
7179 : christian spirituality : 39
15990 : jack : 39
20302 : modern literature : 39
23979 : pop sci : 39
4356 : best of 2015 : 39
1711 : adventures : 39
25628 : relationship : 39
20075 : military war : 38
28030 : social psychology : 38
5506 : botm : 38
15462 : indian author : 38
8214 : cooking and food : 38
29466 : teen lit : 38
19689 : meg cabot : 38
16135 : jamespatterson : 38
9546 : disaster : 38
16978 : keeper : 38
32023 : waiting for release : 38
21035 : myths : 38
3219 : asian american : 38
13079 :

17466 : ku : 22
10826 : erotica bdsm : 22
17408 : komiksy : 22
5565 : boxall 1001 : 22
27822 : single parent : 22
2149 : alphas : 22
2145 : alphabet mysteries : 22
30281 : thieves : 22
6614 : charlaine harris : 22
14283 : here be dragons : 22
6877 : children literature : 22
19784 : mental : 22
30473 : timetravel : 22
90 : 01 folklore : 22
2707 : anthropomorphism : 22
24074 : postcolonial : 22
22064 : npr : 22
6999 : chile : 22
24092 : potter : 22
2604 : anita blake vampire hunter : 22
2600 : anita : 22
14242 : help : 22
31749 : vampires werewolves : 22
21888 : norwegian : 22
14002 : harris charlaine : 22
8624 : cs lewis : 22
15505 : indonesia : 22
18606 : lost generation : 22
6504 : celtic : 22
24241 : presidential bios : 22
13339 : golden books : 22
24236 : president : 22
9389 : devotionals : 22
27011 : seattle : 22
27025 : second world war : 22
919 : 20s : 22
20176 : missing : 22
16798 : juvenil : 22
23248 : pennsylvania : 22
7183 : christian suspense : 22
12165 : folktales : 22
2648

...

19460 : matreidsla 2017 : 1
19458 : matica : 1
19457 : maths science : 1
19455 : mathias malzieu : 1
19453 : matheson : 1
19451 : mathematical : 1
19489 : max barry : 1
19490 : max books : 1
19492 : max frisch : 1
19495 : maximum : 1
19516 : may the force be with you : 1
19512 : may december romance : 1
19511 : may december : 1
19510 : may 2017 : 1
19505 : may 2012 inventory : 1
19501 : maximum ride vol 1 : 1
19499 : maximum ride manga : 1
19497 : maximum ride 1 : 1
19448 : math history : 1
19540 : mayle peter : 1
19391 : mary lawson : 1
19407 : masada : 1
19401 : mary westmacott : 1
19400 : mary todd lincoln : 1
19395 : mary queen of scots : 1
19394 : mary poppins : 1
19392 : mary o hara : 1
19387 : mary hoffman : 1
19443 : mates dates 1 : 1
19386 : mary higgins clarke : 1
19381 : mary e pearson : 1
19379 : mary doria russell : 1
19377 : mary boleyn : 1
19376 : mary beth chapman : 1
19375 : mary anning : 1
19372 : marx : 1
19371 : marvelcomics : 1
19408 : masallar : 1
19409 : masami t

20399 : monographs : 1
20360 : moma : 1
20357 : mom s shelf : 1
20354 : mom lit : 1
20352 : mom books : 1
20350 : molokai : 1
20348 : molly moon : 1
20346 : molly harper : 1
20342 : molecular : 1
20341 : moldova : 1
20340 : moksh : 1
20336 : moira young : 1
20335 : moines : 1
20334 : mohsin hamid : 1
20333 : mohini : 1
20332 : mohawk : 1
20331 : mohammed : 1
20359 : mom upper : 1
20361 : momentarily put aside : 1
20398 : monograph : 1
20387 : mongol : 1
20386 : money personal finance : 1
20385 : money money money : 1
20382 : money laundering : 1
20381 : money finance : 1
20380 : money business : 1
20379 : money books : 1
20378 : money and the law of attraction : 1
20373 : monastery : 1
20372 : monasteries : 1
20370 : monarch butterflies : 1
20369 : monarch 2015 : 1
20367 : mommys books : 1
20366 : mommyhood : 1
20365 : mommy s : 1
16499 : john constantine : 1
16497 : john cleaver : 1
16495 : john carter of mars : 1
12684 : funny in farsi : 1
12699 : futebol : 1
12697 : fushigi yuugi : 

10832 : erskine caldwell : 1
10833 : erstkontakt : 1
10837 : escape from furnace : 1
10838 : escape the ordinary 2015 : 1
10875 : espiritual : 1
10867 : espionage crime : 1
10865 : esperanza rising : 1
10858 : espanha : 1
10855 : esoterismo : 1
10854 : esoterik : 1
10853 : esoterie : 1
10851 : esoteric spirituality : 1
10850 : esoteric philosophy or science : 1
10848 : escuela : 1
10847 : escritores mexicanos : 1
10844 : escola : 1
10843 : escher : 1
10841 : escapology reviews : 1
10840 : escapism : 1
10839 : escaped convict : 1
10975 : eventyr kunst : 1
11073 : expose : 1
11084 : eye candy : 1
11082 : extreme sports : 1
11081 : extreme horror : 1
11080 : extraterrestrial : 1
11078 : extra : 1
11075 : extinct : 1
11074 : exrtrordinary extraterrestrials : 1
11072 : explosions : 1
11052 : expensive for my personal budget : 1
11071 : exploring quality : 1
11068 : exploring author : 1
11066 : exploring 20 books : 1
11064 : explore : 1
11063 : exploratology : 1
11060 : exploitation : 1
1105

15413 : in the collection : 1
15414 : in the company of killers : 1
15448 : independence : 1
15447 : indentured servants : 1
15446 : indelible plot : 1
15445 : indebted : 1
15443 : incredible hulk : 1
15442 : incredible : 1
15439 : income inequality : 1
15438 : includes of dimensions universes : 1
15435 : incas : 1
15429 : incantations : 1
15423 : in the stack : 1
15422 : in the pipeline : 1
15421 : in the past : 1
15420 : in the mood : 1
15419 : in the middle of nowhere : 1
15564 : information science : 1
15566 : information studies : 1
15371 : in hopes of bettering : 1
15653 : institutions : 1
15666 : intellectual capital : 1
15664 : integrity : 1
15663 : integration : 1
15662 : insurgent : 1
15660 : instrumental : 1
15657 : instruction cooking : 1
15656 : instruction art : 1
15654 : instituto : 1
15652 : institutional reform : 1
15640 : inspired my writing : 1
15651 : instant messaging : 1
15650 : instant messages : 1
15649 : instant : 1
15648 : instalove : 1
15647 : insta love or l

13846 : hades : 1
13839 : habitats : 1
13837 : habiburrahman el shirazy : 1
13836 : habe ich : 1
13835 : ha tbr challenge : 1
13834 : ha jin : 1
13833 : h storico : 1
13832 : h storia vera : 1
13831 : h2g2 : 1
13830 : h rider haggard : 1
13829 : h p mallory : 1
13826 : h i v e : 1
13823 : h authors : 1
13817 : gymnastics : 1
13814 : gwen hayes : 1
13813 : gwen cooper : 1
13848 : hafalan shalat delisa : 1
13850 : haggadah : 1
13877 : halloween storytime : 1
13851 : haha : 1
13872 : halliday gemma : 1
13871 : halleys comet : 1
13869 : hall 3 : 1
13868 : hall 2 : 1
13867 : halfblood chronicles : 1
13866 : halfblood : 1
13864 : half human half vampire : 1
13863 : half girlfriend : 1
13862 : half girl friend : 1
13861 : half gf : 1
13860 : half : 1
13858 : haldeman joe : 1
13857 : haldeman : 1
13855 : hairy maclary : 1
13854 : hairdresser : 1
13853 : hailey arthur : 1
14294 : herman koch : 1
14299 : hermeneutics : 1
15022 : human animal interactions : 1
14819 : horrible : 1
14816 : horor : 

In [31]:
#Update value of our tags
t_joined = t_joined[~del_filter]

print(t_joined.shape)
t_joined.head()

(27154, 3)


tag_id       tag_name  count
11743   11743        fiction   9097
1642     1642          adult   6604
8055     8055   contemporary   5287
5090     5090          books   4818
1659     1659  adult fiction   4775

In [32]:
#Filter for tags that have been used atleast 10 or more
# NOTE - This cuts down the number of "tag_names" we have from 27,680 >> 4,450

# We are trying  to get high level tag names, therefore doing this kind of trimming doesn't feel too wrong
# (might be wrong here)

t_joined = t_joined[t_joined["count"] >= 10]
t_joined.shape

(4349, 3)

In [33]:
# from sklearn.cluster import KMeans

# num_clusters = 5

# km = KMeans(n_clusters=num_clusters)

# %time km.fit(tfidf_matrix)

# clusters = km.labels_.tolist()

In [34]:
t_sort_tag_name = t_joined.sort_values(by="tag_name")
t_sort_tag_name.head()

tag_id     tag_name  count
27      27   fictitious     19
47      47            0     11
71      71  00 in class     19
90      90  01 folklore     22
98      98   02 fantasy     48

Because our data is in alphabetical order by 'tag_name', creating clusters by iterating through chunks of the data allow us to determine the affinity groups based on the word distanes.


In [35]:
t_sort_tag_name.shape

(4349, 3)

In [36]:
#Due to the large size and getting convergence warnings splitting up the tags into smaller chunks helps the 
#algorithm
tag_split = np.array_split(np.array(t_sort_tag_name['tag_name']),6)

In [37]:
clusters = []
exemplars = []

words = tag_split[0] #Replace this line
print("CHUNK #1 - size : {0}".format(len(words)))
words = np.asarray(words) #So that indexing with a list will work
lev_similarity = -1*np.array([[distance.levenshtein(w1,w2) for w1 in words] for w2 in words])

affprop = sklearn.cluster.AffinityPropagation(affinity="precomputed", damping=0.5)
affprop.fit(lev_similarity)
for cluster_id in np.unique(affprop.labels_):
    exemplar = words[affprop.cluster_centers_indices_[cluster_id]]
    cluster = np.unique(words[np.nonzero(affprop.labels_==cluster_id)])
    cluster_str = ", ".join(cluster)

    #Add to list for dataframe creation
    clusters.append(cluster)
    exemplars.append(exemplar)

    print(" - *%s:* %s" % (exemplar, cluster_str))
    print()

    


CHUNK #1 - size : 725


/opt/anaconda3/lib/python3.7/site-packages/sklearn/cluster/_affinity_propagation.py:152: FutureWarning: 'random_state' has been introduced in 0.23. It will be set to None starting from 0.25 which means that results will differ at every function call. Set 'random_state' to None to silence this warning, or to 0 to keep the behavior of versions <0.23.
  FutureWarning)


 - *0:* 0, 0wn, 1, 100, 1001, 2, 20s, 3, 39, 80s, 9 11, a, b, c

 - *1 star:* 01 folklore, 1 star, 3 star, 4 star, 5 star, bolitar

 - *100 best books of all time:* 100 best books of all time

 - *100 best business books:* 100 best business books

 - *1000 books before kindergarten:* 1000 books before kindergarten

 - *1001 books:* 100 books, 1001 books, 1001 books list, 1001 import, 1001 list, 1001books, bbc 100 books, biker books

 - *1001 children s books:* 1001 children s books, 1001 childrens books

 - *30 before 30:* 1001 before you die, 30 before 30, before 30

 - *a song of ice and fire:* a song of ice and fire

 - *aar top 100:* aar top 100, amazon 100, amazon top 100, bbc top 100, boxall 1001

 - *action:*  fictitious, abduction, academic, action, action packed, actor, actors, adaptation, addiction, adoption, amazon, arizona, armstrong, asoiaf, atwood, autism, aviation, backlog, batman, beautiful, canon, cartoon, cartoons

 - *adult fantasy:* 02 fantasy, adult fantasy, adult 

In [38]:
words = tag_split[1] #Replace this line
print("CHUNK #2 - size : {0}".format(len(words)))
words = np.asarray(words) #So that indexing with a list will work
lev_similarity = -1*np.array([[distance.levenshtein(w1,w2) for w1 in words] for w2 in words])

affprop = sklearn.cluster.AffinityPropagation(affinity="precomputed", damping=0.5)
affprop.fit(lev_similarity)
for cluster_id in np.unique(affprop.labels_):
    exemplar = words[affprop.cluster_centers_indices_[cluster_id]]
    cluster = np.unique(words[np.nonzero(affprop.labels_==cluster_id)])
    cluster_str = ", ".join(cluster)

    #Add to list for dataframe creation
    clusters.append(cluster)
    exemplars.append(exemplar)

    print(" - *%s:* %s" % (exemplar, cluster_str))
    print()

    


CHUNK #2 - size : 725


/opt/anaconda3/lib/python3.7/site-packages/sklearn/cluster/_affinity_propagation.py:152: FutureWarning: 'random_state' has been introduced in 0.23. It will be set to None starting from 0.25 which means that results will differ at every function call. Set 'random_state' to None to silence this warning, or to 0 to keep the behavior of versions <0.23.
  FutureWarning)


 - *chapter books:* chapter book, chapter books, charles bukowski, charles dickens, early chapter books, erin hunter books

 - *chick lit:* chic lit, chick flick, chick lit, chick lits, chicklit, chiclit, child lee, child lit, chuck palahniuk, church history, civil rights, czech lit, czech republic, dirk pitt

 - *chief inspector armand gamache:* chief inspector armand gamache

 - *childhood faves:* childhood faves, childhood favs, childhood friends, childhood memories, childhood nostalgia

 - *children classics:* childhood classics, children classics, children s classics, childrens classics, christian classics

 - *children lit:* child development, children lit, children s, children s lit, children teen, children youth, childrens, childrens lit, european lit

 - *children literature:* children literature, children picture, children s literature, childrens literature, chinese literature, christian literature, egyptian literature, european literature

 - *children s chapter books:* chil

In [39]:
tag_split[2] 

array(['female detective', 'female lead', 'female pov',
       'female protagonist', 'female writers', 'feminism', 'feminismo',
       'feminist', 'feminist books', 'feminist lit',
       'feminist literature', 'fey', 'fic', 'fictie', 'fiction',
       'fiction adult', 'fiction adventure', 'fiction and literature',
       'fiction christian', 'fiction classic', 'fiction classics',
       'fiction contemporary', 'fiction crime', 'fiction fantasy',
       'fiction general', 'fiction historical', 'fiction horror',
       'fiction humor', 'fiction literature', 'fiction mystery',
       'fiction romance', 'fiction sci fi', 'fiction scifi',
       'fiction short stories', 'fiction suspense', 'fiction thriller',
       'fictitious', 'fighter', 'fighters', 'fiksi', 'fiksi indonesia',
       'film', 'films', 'filosofi', 'filosofia', 'filosofie', 'finance',
       'finance and economics', 'finance business', 'finance economics',
       'finances', 'financial', 'fine art', 'first contact',
      

In [ ]:
words = tag_split[2] #Replace this line
print("CHUNK #3 - size : {0}".format(len(words)))
words = np.asarray(words) #So that indexing with a list will work
lev_similarity = -1*np.array([[distance.levenshtein(w1,w2) for w1 in words] for w2 in words])

affprop = sklearn.cluster.AffinityPropagation(affinity="precomputed", damping=0.5)
affprop.fit(lev_similarity)
for cluster_id in np.unique(affprop.labels_):
    exemplar = words[affprop.cluster_centers_indices_[cluster_id]]
    cluster = np.unique(words[np.nonzero(affprop.labels_==cluster_id)])
    cluster_str = ", ".join(cluster)

    #Add to list for dataframe creation
    clusters.append(cluster)
    exemplars.append(exemplar)

    print(" - *%s:* %s" % (exemplar, cluster_str))
    print()

    


In [41]:
words = tag_split[3] #Replace this line
print("CHUNK #4 - size : {0}".format(len(words)))
words = np.asarray(words) #So that indexing with a list will work
lev_similarity = -1*np.array([[distance.levenshtein(w1,w2) for w1 in words] for w2 in words])

affprop = sklearn.cluster.AffinityPropagation(affinity="precomputed", damping=0.5)
affprop.fit(lev_similarity)
for cluster_id in np.unique(affprop.labels_):
    exemplar = words[affprop.cluster_centers_indices_[cluster_id]]
    cluster = np.unique(words[np.nonzero(affprop.labels_==cluster_id)])
    cluster_str = ", ".join(cluster)

    #Add to list for dataframe creation
    clusters.append(cluster)
    exemplars.append(exemplar)

    print(" - *%s:* %s" % (exemplar, cluster_str))
    print()

    


CHUNK #4 - size : 725


/opt/anaconda3/lib/python3.7/site-packages/sklearn/cluster/_affinity_propagation.py:152: FutureWarning: 'random_state' has been introduced in 0.23. It will be set to None starting from 0.25 which means that results will differ at every function call. Set 'random_state' to None to silence this warning, or to 0 to keep the behavior of versions <0.23.
  FutureWarning)


 - *july 2013:* judy blume, julia quinn, july 2013, june 2013, just for fun, may 2013

 - *karen kingsbury:* karen kingsbury, karen kingsbury books, mary higgins clark

 - *karen slaughter:* karen slaughter, karin slaughter, kay scarpetta, marvel unlimited

 - *kathy reichs:* kate daniels, kathy reichs, kathy reichs bones, lahaye jenkins

 - *kelley armstrong:* karen marie moning, kelley armstrong, kelly armstrong

 - *ken follet:* ken follet, ken follett, kurt vonnegut, need to get, nelson demille, net galley, new adult, new thought

 - *kick ass heroine:* kick ass heroine, kick ass heroines, kickass heroine

 - *kid lit:* kid lit, kid stuff, kiddie lit, kidlit, kidnapping, kids lit, kindergarten, kinsella, kleypas lisa, lit fic, mi biblioteca, myron bolitar, neil gaiman, nihilism

 - *kids books:* kid books, kid s books, kids books, kids chapter books, kids shelf, kids stuff, kinderboeken, lds books, leadership books, nook book

 - *kinsey milhone:* kinsey milhone, kinsey millhone

 

In [42]:
words = tag_split[4] #Replace this line
print("CHUNK #5 - size : {0}".format(len(words)))
words = np.asarray(words) #So that indexing with a list will work
lev_similarity = -1*np.array([[distance.levenshtein(w1,w2) for w1 in words] for w2 in words])

affprop = sklearn.cluster.AffinityPropagation(affinity="precomputed", damping=0.5)
affprop.fit(lev_similarity)
for cluster_id in np.unique(affprop.labels_):
    exemplar = words[affprop.cluster_centers_indices_[cluster_id]]
    cluster = np.unique(words[np.nonzero(affprop.labels_==cluster_id)])
    cluster_str = ", ".join(cluster)

    #Add to list for dataframe creation
    clusters.append(cluster)
    exemplars.append(exemplar)

    print(" - *%s:* %s" % (exemplar, cluster_str))
    print()

    


CHUNK #5 - size : 725


/opt/anaconda3/lib/python3.7/site-packages/sklearn/cluster/_affinity_propagation.py:152: FutureWarning: 'random_state' has been introduced in 0.23. It will be set to None starting from 0.25 which means that results will differ at every function call. Set 'random_state' to None to silence this warning, or to 0 to keep the behavior of versions <0.23.
  FutureWarning)


 - *not interested:* not completed, not interested, not out yet, not yet released

 - *nr:* norway, npr, nr, nyc, nyrb, obc, of, on, oz, p, pb, pd, peru, pm, pnr, pnr uf, r, rgrc

 - *on my shelf:* on my shelf, on my shelves, on shelf, on the shelf, our shared shelf

 - *other:* north america, northwest, october 2013, ohio, on deck, on hold, opera, orphans, other, others, otp, outdoor, outdoors, outlander, paper, potter, prophecy, queer, queer lit

 - *other fiction:* other comics, other fiction, other non fiction, other nonfiction, pop fiction, popular fiction, pulitzer fiction, pulp fiction, queer fiction, romantic fiction

 - *paranormal fantasy:* paranormal angels, paranormal fantasy, paranormal fiction, paranormal mystery, paranormal romance, paranormal supernatural, paranormal urban fantasy, paranormal vampires

 - *parenting:* on writing, painting, palahniuk, palestine, paperback, parenthood, parenting, pending, performing, pregnancy parenting, programming, running, sequencing



In [43]:
words = tag_split[5] #Replace this line
print("CHUNK #6 - size : {0}".format(len(words)))
words = np.asarray(words) #So that indexing with a list will work
lev_similarity = -1*np.array([[distance.levenshtein(w1,w2) for w1 in words] for w2 in words])

affprop = sklearn.cluster.AffinityPropagation(affinity="precomputed", damping=0.5)
affprop.fit(lev_similarity)
for cluster_id in np.unique(affprop.labels_):
    exemplar = words[affprop.cluster_centers_indices_[cluster_id]]
    cluster = np.unique(words[np.nonzero(affprop.labels_==cluster_id)])
    cluster_str = ", ".join(cluster)

    #Add to list for dataframe creation
    clusters.append(cluster)
    exemplars.append(exemplar)

    print(" - *%s:* %s" % (exemplar, cluster_str))
    print()

    


CHUNK #6 - size : 724
 - *sherilyn kenyon:* sherilyn kenyon, sherrilyn kenyon

 - *shonen manga:* shojo manga, shonen manga, shoujo manga, shounen manga, showalter gena

 - *short:* shojo, shonen, short, shorts, shoujo, shounen, shreve, skimm, spirit, sport, sports, story, sweet, swoon worthy, thomas, thor, tudor, whodunit, whodunnit

 - *short stories:* sherlock holmes, short stories, short story, shortstories, spy stories, survival stories, utopia dystopia, war stories

 - *short stories essays:* short stories and essays, short stories essays

 - *short story collections:* short story collection, short story collections, story collections

 - *sidney sheldon:* sidney sheldon, sidneysheldon, sydney sheldon

 - *sir arthur conan doyle:* sir arthur conan doyle

 - *social:* sherlockian, shinigami, silly, silva, social, social work, socialism, society, sociology, someday, sonlight, sophia, soviet, suicide, surreal, survival, technical, tortall, utopia

 - *social media:* social commentar

/opt/anaconda3/lib/python3.7/site-packages/sklearn/cluster/_affinity_propagation.py:152: FutureWarning: 'random_state' has been introduced in 0.23. It will be set to None starting from 0.25 which means that results will differ at every function call. Set 'random_state' to None to silence this warning, or to 0 to keep the behavior of versions <0.23.
  FutureWarning)


In [44]:
#Potential clustered genres
genre_clusters = {'Exempler':exemplars,'Cluster':clusters}
df_genre_clusters = pd.DataFrame(genre_clusters)
df_genre_clusters

Exempler  \
0                                 0   
1                            1 star   
2        100 best books of all time   
3           100 best business books   
4    1000 books before kindergarten   
..                              ...   
516                     world war i   
517                             wwi   
518                     young adult   
519             young adult fantasy   
520               zombie apocalypse   

                                               Cluster  
0    [0, 0wn, 1, 100, 1001, 2, 20s, 3, 39, 80s, 9 1...  
1    [01 folklore, 1 star, 3 star, 4 star, 5 star, ...  
2                         [100 best books of all time]  
3                            [100 best business books]  
4                     [1000 books before kindergarten]  
..                                                 ...  
516  [sword laser, world lit, world war 1, world wa...  
517  [sjc, swiss, twd, wlw, woc, wot, wtf, ww 2, ww...  
518  [young adult, young adult lit, young adults, y...  
519  [young adult books, young adult contemporary, ...  
520             [sookie stackhouse, zombie apocalypse]  

[521 rows x 2 columns]

### Progress! 


Essentially we are able to break down the 34,000 plus tags into clustered groups of about 520. From here we can apply another level of processing to try and use the general purpose tags, and from their determine a smaller subset of genres.